# 3. Clustering

https://www.kaggle.com/datasets/manchunhui/us-election-2020-tweets?resource=download

# Import Libraries

In [0]:
!pip install emoji

You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-e3270a88-3c98-4a13-9675-cb163ff098fc/bin/python -m pip install --upgrade pip' command.


In [0]:
from pyspark.sql.functions import lit, col, desc, to_date, length, count, when, hour, dayofweek, round, explode, lower, udf
from pyspark.sql.types import ArrayType, StringType
from pyspark.ml.feature import VectorAssembler, BucketedRandomProjectionLSH
from pyspark.sql.functions import col, count, desc, lit, coalesce, row_number
from pyspark.sql import functions as F
from pyspark.sql import SparkSession
from pyspark.sql.functions import round as spark_round
from pyspark.sql.window import Window
from pyspark.sql import DataFrame
from pyspark.sql.functions import floor
from pyspark.sql.functions import monotonically_increasing_id

import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
import plotly.express as px
from sklearn.impute import KNNImputer
from functools import reduce

import re
import emoji

from pyspark.ml.feature import Tokenizer, StopWordsRemover, HashingTF, IDF, StringIndexer, CountVectorizer

In [0]:
from pyspark.sql import SparkSession
from pyspark.ml.feature import VectorAssembler, PCA
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator
from pyspark.ml.feature import StringIndexer, VectorAssembler, StandardScaler, PCA
from pyspark.ml import Pipeline
import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from matplotlib.colors import ListedColormap
from sklearn.metrics import silhouette_samples, silhouette_score
import numpy as np
import matplotlib.cm as cm
from sklearn.metrics import confusion_matrix
import seaborn as sns

In [0]:
# Initialize Spark session
spark = SparkSession.builder.appName("Clustering").getOrCreate()

# Import Dfs

In [0]:
# # File location and type
# train_file_location = "/FileStore/tables/train.csv"
# val_file_location = "/FileStore/tables/val.csv"
# test_file_location = "/FileStore/tables/test.csv"
# file_type = "csv"

# # CSV options
# infer_schema = "true"
# first_row_is_header = "true"
# delimiter = ","

# # The applied options are for CSV files. For other file types, these will be ignored.
# train_df = (
#     spark.read.format(file_type)
#     .option("inferSchema", infer_schema)
#     .option("header", first_row_is_header)
#     .option("sep", delimiter)
#     .option("quote", '"') # To handle commas correctly
#     .option("escape", '"')
#     .option("multiLine", "true")  # Allow fields to span multiple lines (helps with complex quoted fields)
#     .option("mode", "PERMISSIVE") # Avoid failing on corrupt records
#     .load(train_file_location)
# )

# val_df = (
#     spark.read.format(file_type)
#     .option("inferSchema", infer_schema)
#     .option("header", first_row_is_header)
#     .option("sep", delimiter)
#     .option("quote", '"') # To handle commas correctly
#     .option("escape", '"')
#     .option("multiLine", "true")  # Allow fields to span multiple lines (helps with complex quoted fields)
#     .option("mode", "PERMISSIVE") # Avoid failing on corrupt records
#     .load(val_file_location)
# )

# test_df = (
#     spark.read.format(file_type)
#     .option("inferSchema", infer_schema)
#     .option("header", first_row_is_header)
#     .option("sep", delimiter)
#     .option("quote", '"') # To handle commas correctly
#     .option("escape", '"')
#     .option("multiLine", "true")  # Allow fields to span multiple lines (helps with complex quoted fields)
#     .option("mode", "PERMISSIVE") # Avoid failing on corrupt records
#     .load(test_file_location)
# )

# # Display result
# display(train_df)

In [0]:
# Import train, val and test
train_df = spark.read.format("delta").load("/dbfs/FileStore/tables/train_df")
val_df = spark.read.format("delta").load("/dbfs/FileStore/tables/val_df")
test_df = spark.read.format("delta").load("/dbfs/FileStore/tables/test_df")

# Display train_df
display(train_df)

state state_code lat_bin lon_bin candidate created_at tweet_id tweet likes retweet_count source user_id user_name user_screen_name user_description user_join_date user_followers_count user_location lat long city continent collected_at row_id Mississippi MS 32 -91 trump 2020-11-03T01:42:28.000+0000 1.32344037418306765E18 I lost so many followers and just looked at the stats.. I CANNOT believe how many of our fellow patriots have been suspended!! This is so wrong.. #Trump2020LandslideVictory #Trump 2.0 0.0 Twitter Web App 1.10335996748094259E18 ANNIE Annie38018477 Victim mentality is for the weak. Help when you can and don't second guess it. 
#suicideprevention #KAG #MAGA2020 #veterans #humantrafficking #trump 2019-03-06T18:21:30.000+0000 1879.0 Jackson, MI 32.29903839999999 -90.1847691 Jackson North America 2020-11-05T12:37:49.678+0000 717 Mississippi MS 32 -90 trump 2020-10-23T03:10:45.000+0000 1.31947632777126298E18 But #Trump says they have such care ! https://t.co/YwvATuuFMh 0.0 0.0 Twitter for iPhone 5.86149E8 Lucci mellwit2Ls Instagram @mellwit2Ls #BlackLivesMatter👊🏽 2012-05-20T23:12:21.000+0000 172.0 Mississippi, USA 32.9715645 -89.7348497 Biloxi North America 2020-10-27T17:50:02.150+0000 1158 Mississippi MS 32 -90 trump 2020-11-02T21:17:04.000+0000 1.32337358721925939E18 #Trump2020LandslideVictory 🇺🇸🥓🇺🇸#Trump2020LandslideVictory ❤️#Trump2020LandslideVictory ❤️#Trump2020LandslideVictory 💯 #Trump #TrumpTrain 🚄#TeaParty 🥳 https://t.co/O7hkMAYNYL 1.0 0.0 Twitter for iPad 5.42986589E8 ❌BOTrl77❌ ImaFreespeaker He healed my body,🎶He touch my mind,🎶He saved me just N time! I😆,🥰,🙏& 🙌🏻,America=freedom,love it or leave it! ♥️ #KAG2020 🇺🇸🥓🇺🇸..GOD BLESS AMERICA! 2012-04-02T01:01:05.000+0000 5214.0 Mississippi, USA 🇺🇸🥓🇺🇸 32.9715645 -89.7348497 Biloxi North America 2020-11-03T14:25:16.282+0000 2745 Mississippi MS 31 -92 trump 2020-10-23T02:48:25.000+0000 1.31947070629239194E18 #Biden got him good real good so it will be the end of #trump 0.0 0.0 Twitter for Android 1.625923531E9 Carrington Jackson RealCarrington Mississippi 🇺🇸 #SMTTT
Martial Artist 🥋
skilled of a martial artist 
formal 2nd place world 🏆
❤🎧🎶#hiphophead #Metalhead 
#FuckRacism #BLACKLIVESMATTER 2013-07-27T17:08:30.000+0000 756.0 Natchez, MS 31.5604442 -91.403171 Biloxi North America 2020-10-27T17:50:22.343+0000 5924 Mississippi MS 32 -90 trump 2020-10-22T03:52:03.000+0000 1.31912433288753971E18 After the election. If #trump wins because of the misinterpreted #latinovote? Do you realize what will happen to the #relationship between #blacks and Latinos?
 It 
Will
Be 
Destroyed. 
#dontvoteforachildseparatingracist 0.0 0.0 Twitter for Android 1.20811244753142989E18 Anthonyquintin2020 Anthonyquintin5 6'7 with a big heart♡
Retired♡♡
Father of Paws♡♡♡ 2019-12-20T19:50:40.000+0000 42.0 Mississippi, USA 32.9715645 -89.7348497 Biloxi North America 2020-10-27T17:57:37.556+0000 6983 Mississippi MS 32 -90 trump 2020-11-03T23:01:42.000+0000 1.32376230526861722E18 Where’s everyone getting election results? Google has some NH results showing but that’s it. #ElectionDay #Election2020 #Trump2020 #Trump 0.0 0.0 Twitter Web App 1.09483951445817754E18 Jerome Kelly jklibertarian I've joined the Libertarian Party. Most importantly I’m anti socialist. Prior soldier and prior photojournalist. Grinding in a factory now. 2019-02-11T06:04:16.000+0000 308.0 Mississippi, USA 32.9715645 -89.7348497 Biloxi North America 2020-11-05T12:22:31.795+0000 7048 Mississippi MS 30 -89 trump 2020-10-19T23:14:38.000+0000 1.31832974372552704E18 @jvgraz It's even worse than that. Voting for #Biden, in particular, isn't even a stamp of approval; it's fearful submission to #bluemail. "Submit or you get #Trump!" Whereas voting for the #GreenParty (or #PSL) is a statement of defiance. #VoteGreen 
https://t.co/MtbLmzd4zW 18.0 2.0 Twitter for Android 4.16490624E8 Douglas Edwards↙️🚩🦺🌹🌻 mastodon.social/@dedicto SebastosPublius https://t.co/J7ye28C20W 2011-11-19T19:24:25.000+0000 2036.0 Biloxi, Mississippi, USA 30.374672999

In [0]:
train_df.printSchema()

root
 |-- state: string (nullable = true)
 |-- state_code: string (nullable = true)
 |-- lat_bin: long (nullable = true)
 |-- lon_bin: long (nullable = true)
 |-- candidate: string (nullable = true)
 |-- created_at: timestamp (nullable = true)
 |-- tweet_id: double (nullable = true)
 |-- tweet: string (nullable = true)
 |-- likes: double (nullable = true)
 |-- retweet_count: double (nullable = true)
 |-- source: string (nullable = true)
 |-- user_id: double (nullable = true)
 |-- user_name: string (nullable = true)
 |-- user_screen_name: string (nullable = true)
 |-- user_description: string (nullable = true)
 |-- user_join_date: timestamp (nullable = true)
 |-- user_followers_count: double (nullable = true)
 |-- user_location: string (nullable = true)
 |-- lat: double (nullable = true)
 |-- long: double (nullable = true)
 |-- city: string (nullable = true)
 |-- continent: string (nullable = true)
 |-- collected_at: timestamp (nullable = true)
 |-- row_id: long (nullable = true)



# Clustering

In [0]:
# Assemble feature columns into a single vector
feature_cols = [
    'likes',
    'retweet_count'
]
assembler = VectorAssembler(inputCols=feature_cols, outputCol="features")

# Standardize the features
scaler = StandardScaler(
    inputCol="features",
    outputCol="scaled_features",
    withMean=True,
    withStd=True
)

In [0]:
# Create and run the pipeline
pipeline = Pipeline(stages=[assembler, scaler])
pipeline_model = pipeline.fit(train_df)

# Transform the data using the fitted pipeline
processed_train_df = pipeline_model.transform(train_df)

+---------+-----------+
|candidate|label_index|
+---------+-----------+
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
|trump    |0.0        |
+---------+-----------+
only showing top 20 rows



In [0]:
# Apply KMeans clustering
kmeans = KMeans(
    featuresCol="scaled_features",
    predictionCol="cluster",
    k=3,
    seed=42
)

# Fit model
kmeans_model = kmeans.fit(processed_df)

# Make predictions
clustered_df = kmeans_model.transform(processed_df)

# Display a few results
clustered_df.select("likes", "retweet_count", "cluster").display()

In [0]:
# Visual inspection
clustered_df.groupBy("cluster").count().orderBy("count", ascending=False).show()

In [0]:
# Convert to Pandas
pdf = processed_df.select("scaled_features", "cluster").toPandas()

In [0]:
# Plot setup
plt.figure(figsize=(10, 7))
sns.set(style="whitegrid", font_scale=1.2)

# Custom color palette and markers
palette = sns.color_palette("Set2", 3)
markers = ['o', 's', 'D']  # circle, square, diamond

# Plot points with custom markers for each label
for i, cluster in enumerate(pdf["cluster"].unique()):
    subset = pdf[pdf["cluster"] == label]
    plt.scatter(subset["x"], subset["y"], 
                label=label, 
                marker=markers[i % len(markers)], 
                s=80, 
                alpha=0.8, 
                edgecolor='k')

# Finalize plot
plt.title("Advanced PCA Plot of Iris Dataset")
plt.xlabel("Principal Component 1")
plt.ylabel("Principal Component 2")
plt.legend(title="Iris Species / Cluster")
plt.tight_layout()
plt.show()

# Export Dataframe

In [0]:
# Export train DataFrame as a Delta table
train_df.write.mode("overwrite") \
    .option("overwriteSchema", "true") \
    .format("delta") \
    .save("/dbfs/FileStore/tables/train_df")

# Export val DataFrame as a Delta table
val_df.write.mode("overwrite") \
    .option("overwriteSchema", "true") \
    .format("delta") \
    .save("/dbfs/FileStore/tables/val_df")

# Export test DataFrame as a Delta table
test_df.write.mode("overwrite") \
    .option("overwriteSchema", "true") \
    .format("delta") \
    .save("/dbfs/FileStore/tables/test_df")

Out[144]: 970919

In [0]:
train_df.display()